<a href="https://colab.research.google.com/github/MTRL-studio/mtrl-3d-scripts/blob/main/models/colab/MTRL_Ripple_Tube_Solid_PETG.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# FullControl design template

*<<< check out demo models [here](https://github.com/FullControlXYZ/fullcontrol/tree/master/models/README.md) >>>*
  
press ctrl+F9 to run all cells in this notebook, or press shift+enter to run each cell sequentially

if you change one of the code cells, make sure you run it and all subsequent cells again (in order)

*this document is a jupyter notebook - if they're new to you, check out how they work: [link](https://www.google.com/search?q=ipynb+tutorial), [link](https://jupyter.org/try-jupyter/retro/notebooks/?path=notebooks/Intro.ipynb), [link](https://colab.research.google.com/)*
### be patient :)

the next code cell may take a while because running it causes several things to happen:
- connect to a google colab server -> download the fullcontrol code -> install the fullcontrol code

check out [other tutorials](https://github.com/FullControlXYZ/fullcontrol/blob/master/tutorials/README.md) to understand the python code for the FullControl design

In [ ]:
if 'google.colab' in str(get_ipython()):
  !pip install git+https://github.com/FullControlXYZ/fullcontrol --quiet
import fullcontrol as fc
from google.colab import files

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
# printer/gcode parameters

design_name = 'mtrl_ripple_lamp_0.8n_PETG'
nozzle_temp = 255      # Much hotter. 0.8mm nozzle needs high heat to flow PETG smoothly.
bed_temp = 75          # Hotter bed to prevent warping (PETG loves to lift at corners).
print_speed = 2400     # Slower (40mm/s).
                       # Why? PETG needs time to bond. If you go too fast, it becomes cloudy/matte.
                       # Slow speed = High Gloss "Glass" look.
fan_percent = 30       # CRITICAL: 100% fan will make PETG crack. 30% is enough for overhangs.
printer_name='bambulab_x1'

In [ ]:
import math

# --- 1. Printer Settings (Optimized for 0.8mm Nozzle) ---
EW = 0.90          # Extrusion Width (Slightly wider than nozzle for strength)
EH = 0.5           # Layer Height (Big, chunky layers for speed and optical effect)
initial_z = EH*0.6 # Squish for bed adhesion

# --- 2. Scale & Dimensions ---
SCALE = 3.0        # 300% Scale
base_radius = 15   # Original radius of the demo model
base_height = 40   # Original height of the demo model

# Calculate the new real-world dimensions
radius = base_radius * SCALE
total_height = base_height * SCALE

# Automatic Layer Calculation
layers = int(total_height / EH)

# --- 3. Ripple Texture Settings ---
# You might want fewer ripples with a fat nozzle so they don't get muddy
ripples_per_layer = 12
ripple_amplitude = 2.0
twist_angle = 0.2

In [ ]:
steps = []
# Points per layer (Lowered slightly since 0.8mm nozzle loses fine detail anyway)
steps_per_layer = int(80 * SCALE)

for layer in range(layers):
    # BASE Z for this layer
    layer_z_start = (layer * EH) + initial_z

    # Create one full circle (loop)
    for i in range(steps_per_layer):
        # Percentage around the circle (0.0 to 1.0)
        t = i / steps_per_layer
        angle = t * 2 * math.pi

        # --- THE Z-SPIRAL FIX ---
        # Continuous rise to prevent vertical seam
        current_z = layer_z_start + (t * EH)

        # --- THE RIPPLE "PHASE" FIX ---
        # Continuous twist to prevent side-seam
        continuous_layer_value = layer + t
        phase_shift = continuous_layer_value * twist_angle

        # Calculate the offset
        offset = ripple_amplitude * math.sin((angle * ripples_per_layer) + phase_shift)

        # Apply offset to the radius
        current_radius = radius + offset

        # Convert Polar to Cartesian
        x = current_radius * math.cos(angle)
        y = current_radius * math.sin(angle)

        steps.append(fc.Point(x=x, y=y, z=current_z))

In [ ]:
# preview the design
# Note: The 'tube' style plot will now look much thicker/bolder
fc.transform(steps, 'plot', fc.PlotControls(style='tube', zoom=0.7, initialization_data={'extrusion_width': EW, 'extrusion_height': EH}))

In [ ]:
# generate and save gcode
gcode_controls = fc.GcodeControls(
    printer_name=printer_name,
    initialization_data={
        'print_speed': print_speed,
        'nozzle_temp': nozzle_temp,
        'bed_temp': bed_temp,
        'fan_percent': fan_percent,
        'extrusion_width': EW,
        'extrusion_height': EH
    }
)

gcode = fc.transform(steps, 'gcode', gcode_controls)
filename = f'{design_name}.gcode'
with open(filename, 'w') as f:
    f.write(gcode)

print(f"Success! Downloaded {filename}")
files.download(filename)

#### please tell us what you're doing with FullControl!

- tag FullControlXYZ on social media ([twitter](https://twitter.com/FullControlXYZ), [instagram](https://www.instagram.com/fullcontrolxyz/), [linkedin](https://www.linkedin.com/in/andrew-gleadall-068587119/), [tiktok](https://www.tiktok.com/@fullcontrolxyz))
- email [info@fullcontrol.xyz](mailto:info@fullcontrol.xyz)
- post on the [subreddit](https://reddit.com/r/fullcontrol)
- post in the [github discussions or issues tabs](https://github.com/FullControlXYZ/fullcontrol/issues)

in publications, please cite the original FullControl paper and the github repo for the new python version:

- Gleadall, A. (2021). FullControl GCode Designer: open-source software for unconstrained design in additive manufacturing. Additive Manufacturing, 46, 102109.
- Gleadall, A. and Leas, D. (2023). FullControl [electronic resource: python source code]. available at: https://github.com/FullControlXYZ/fullcontrol